In [1]:
import nltk
import numpy as np
import scipy as sc
import sklearn
import pytesseract
import wordcloud
import gensim
import pymysql
import json
import bisect
from sklearn.metrics import pairwise_distances
from sklearn.metrics.pairwise import cosine_similarity
from autocorrect import spell
from spellchecker import SpellChecker
from nltk.stem.snowball import SnowballStemmer
from nltk.tokenize import word_tokenize
import re, regex
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.tag import pos_tag
import pickle

A lot of imports, half of them are probably unnecessary.

Connecting to database

In [2]:
import pymysql.cursors
connection = pymysql.connect(host='webirfacts.csdsyolim34i.us-east-2.rds.amazonaws.com',
                             user='group5',
                             password='aws12345',
                             db='facts_8',
                             charset='utf8mb4',
                             cursorclass=pymysql.cursors.DictCursor)

Downloading the gensim word2vec model

In [3]:
from gensim.test.utils import common_texts, get_tmpfile
from gensim.models import Word2Vec
# path = get_tmpfile("word2vec.model")

# model = Word2Vec(common_texts, size=100, window=5, min_count=1, workers=4)
# model.save("word2vec.model")

In [1]:
# Not to be run if we pickle the model
model = gensim.models.KeyedVectors.load_word2vec_format('./GoogleNews-vectors-negative300.bin', binary=True)

NameError: name 'gensim' is not defined

In [22]:
# pickling the model
# import pickle
# with open('model_word2vec.sav', 'wb') as f:
#     pickle.dump(model, f)

In [4]:
# loading the model from pickle
# Delyana, change the file name here to the one where you keep the model
with open('model_word2vec.sav', 'rb') as f:
    model = pickle.load(f)

Playing around with a model

In [ ]:
word_vectors = model
count = 0
for word in word_vectors.vocab:
    if count<100:
        print(word)
        count += 1
    else:
        break

In [105]:
model.most_similar(positive="query", topn=5)

[('queries', 0.7984702587127686),
 ('querying', 0.5786418914794922),
 ('querry', 0.5779199600219727),
 ('story_emailsportsfeedback@thomsonreuters.com', 0.5712707042694092),
 ('question', 0.547287106513977)]

In [214]:
model.doesnt_match(["government","corruption","peace","war"])

'peace'

### Indexing part (pre-processing)

Part for creating index and idf scores for the words.

Should not be run in the app as all the information from here is read from files.

In [6]:
#Get all the entries from database
with connection.cursor() as cursor:
        sql = "SELECT * from clean_text"
        cursor.execute(sql)
        all_documents = cursor.fetchall()

# Creating the list of all words
words_list = []
for row in all_documents:
    words_list.extend(row['clean_data'].split())
words = set(words_list)
words = sorted(words)

# Adding the words to dictionary document by document (creating index)
dictionary = {key: [[],[]] for key in words}
for row in all_documents:
    words_in_doc = row['clean_data'].split()
    for i, word in enumerate(words_in_doc):
        dictionary[word][0].append(row['doc_id'])
        dictionary[word][1].append(i)

# Saving index to file
with open('index_8facts_clean.json', 'w') as fp:
    json.dump(dictionary, fp)

In [76]:
# Not the optimal way in terms of processing time to create a dictionary. The next snippet of code should be used.
idf_dict = {key: np.log(len(doc_vectors)/words_list.count(key)) for key in words}

# Saving idf frequencies into file
with open('idf_8facts_clean.json', 'w') as fp:
    json.dump(idf_dict, fp)

10.484375


In [10]:
# Code for creating idf dictionary
from collections import defaultdict
counted = defaultdict(int)
for i,v in enumerate(words_list):
    counted[v] += 1

idf_dict = {key: np.log(len(all_documents)/counted[key]) for key in words}
# Saving idf frequencies into file
with open('idf_8facts_clean.json', 'w') as fp:
    json.dump(idf_dict, fp)  


### Reading from files

In [12]:
# Read the index from file
with open('index_8facts_clean.json', 'r') as fp:
    dictionary = json.load(fp)
    
# Read the idf scores from file
with open('idf_8facts_clean.json', 'r') as fp:
    idf_dict = json.load(fp)
    
# Read the document vectors, constructed using idf
with open('docs_vectors_idf_8facts.pk', 'rb') as f:
    doc_vectors_idf = pickle.load(f)

### Lemmatization and text cleaning (taken from Deb)

In [13]:
# Initilizing spellChecker and lemmatizer
spell = SpellChecker()
lemmatizer = WordNetLemmatizer()

In [14]:
# Dictionaty of parts of speech
pos_dict = { 'None':'n', '$':'n' ,'CC':'n', 'CD':'n', 'DT':'n', 'EX': 'n', 'FW': 'n', 'IN':'n', 'JJ': 'a', 'JJR':'a', 'JJS':'a',
                 'LS': 'n','MD': 'n','NN': 'n','NNS': 'n','NNP': 'n','NNPS': 'n','PDT': 'r','POS': 'n','PRP': 'n','PRP$': 'n','RB': 'r','RBR': 'r','RBS': 'r',
        'RP': 'n','TO': 'n','UH': 'n', 'VB': 'v', 'VBD': 'v','VBG': 'v', 'VBN': 'v','VBP': 'v','VBZ': 'v','WDT': 'n','WP': 'n','WP$': 'n','WRB': 'n', 'SYM': 'n'}
# Cleaning the query (dollars, percents, stopwords), not including punctuation
def clean_query(query):
    currency_dict = {'$': 'dollar', '€': 'euro', '₨': 'rupee', '¢' : 'cent', '£': 'pound', '¥': 'yen'}
    currency_list = regex.findall(r'\p{Sc}', query)
    clean_text = ""
    if (len(currency_list) != 0):
        for currency in currency_list:
        #     find at which position does the currency exist
            position = query.find(currency)
            if (position != -1):
                query = query[:position] + currency_dict[currency] + " "+ query[position:]

    # replace % by "percent" word
    def findOccurrences(s, ch):
        return [i for i, letter in enumerate(s) if letter == ch]
    
    percent_position = findOccurrences(query,'%')
    if not percent_position:
        for pos in percent_position:
            query = query[:percent_position] + " percent " + query[percent_position:]

    # remove the stopwords here
    stopwords_list = stopwords.words('english')
    # print("stopwords = "+str(stopwords_list))
    for word in word_tokenize(query):
        if word.lower() not in stopwords_list and len(word) != 1 or word.isdigit() == True:
            clean_text += word + " "
        # else:
            # print(str(word) + " is stopword")
    clean_text = clean_text.lstrip().rstrip()
    return clean_text

# Lemmatizing query --- used everywhere right after clean_query except searching in word2vec for compound entries (like Aleksandr_Lukashenko)
def lemmatize_query(query):
    # get the pos tags first
    query_pos_tag =  pos_tag(query)
    query_string = " ".join(query)
    pos_tag_dict = {}
    # creating a dictionary of POS tags which will be used below
    for tags in query_pos_tag:
        clean_word = re.sub('[^\w\s]', '', tags[0])
        pos_tag_dict[clean_word] = tags[1]

    english_text = ""
    # print(pos_tag_dict)
    for word in query:
#         here we have to perform spell check on the word
            # convert each word to its root form
        conv_pos_tag = str(pos_tag_dict.get(word))
        lemmatized_word = lemmatizer.lemmatize(word, pos = pos_dict.get(conv_pos_tag))
            # print("For " + str(word) + " is english word")
            # print(str(word) + ":"+str(lemmatized_word))
        english_text += lemmatized_word+" "

    # removing punctuation marks
    # doing this here  since we do not want to eliminate the hyphen-ated words
    english_text = re.sub('[^\w\s]', ' ', english_text)

    final_text = english_text.lstrip().rstrip().split()
    # return english_text
    return final_text

### Document to Vector methods

In [15]:
# Method, converting document (or query) to vector, averaging the words vectors from it
# Not used anymore as modified function from below is used
def doc2vec(words):
    word_vectors = []
    for word in words:
        if word in model.vocab:
            word_vectors.append(model[word])
        else:
            if word.capitalize() in model.vocab:
                word_vectors.append(model[word.capitalize()])
    if not word_vectors:
        return np.repeat(0,300)
    return np.mean(word_vectors, axis = 0)

# Method, converting document (or query) to vector, averaging the words vectors from it, using idf 
def doc2vec_idf(words):
    word_vectors = []
    for word in words:
        if word in model.vocab:
            word_vectors.append(model[word])
            if word in idf_dict.keys():
                word_vectors[len(word_vectors)-1] = word_vectors[len(word_vectors)-1]*idf_dict[word]
            else:
                word_vectors[len(word_vectors)-1] = word_vectors[len(word_vectors)-1]*max(idf_dict.values())
        else:
            if word.capitalize() in model.vocab:
                word_vectors.append(model[word.capitalize()])
                if word in idf_dict.keys():
                    word_vectors[len(word_vectors)-1] = word_vectors[len(word_vectors)-1]*idf_dict[word]
                else:
                    word_vectors[len(word_vectors)-1] = word_vectors[len(word_vectors)-1]*max(idf_dict.values())
    if not word_vectors:
        return np.repeat(0,300)
    return np.mean(word_vectors, axis = 0)

### Search in Index

In [16]:
# Method for searching query in index, step is the maximum distance between the words from the query in the document 
def search_index(query, index = dictionary, step = 3):
    query = clean_query(query)
    if query== '':
        return []
    query_words = query.split()
    lemmatized_query = lemmatize_query(query_words)
    lowercase_query = [word.lower() for word in lemmatized_query]
    # If it's just one word we search it in the index and return the documents or empty set
    if len(query_words) == 1:
        if lowercase_query[0] in index.keys():
            return [[x, 1] for x in np.unique(index[lowercase_query[0]][0])]
        else:
            return []
    else:
        # For more than 1 word queries we search for the documents where each one appears and create common documents
        query_vector = doc2vec_idf(lowercase_query)
        doc_ids = []
        positions = []
        satisfying_docs = []
        for word in lowercase_query:
            if word in index.keys():
                doc_ids.append(index[word][0])
                positions.append(index[word][1])
            else:
                doc_ids.append([])
                positions.append([])
        common_docs = set.intersection(*map(set,doc_ids))
        docs_appearences = [doc for docs in [np.unique(x) for x in doc_ids] for doc in docs]
        docs_freq = count_frequency(docs_appearences)
        # We check if in the common documents they appear in the correct order with correct step
        if common_docs:
            for doc in common_docs:
                word_positions = []
                for i in range(0,len(doc_ids)):
                    word_positions.append(list(np.array(positions[i])[np.array(doc_ids[i]) == doc]))
                if dfs(word_positions, 0, 0, step):
                    satisfying_docs.append([doc,1])
                else:
                    # Returning this if the step or order is not correct
                    satisfying_docs.append([doc,0.95])
        # For every document in which less than all the words from query found, we do this loop
        for doc in docs_freq:
            if doc[1] < len(query_words):
                cos_sim = cosine_similarity([query_vector], [doc_vectors_idf[doc[0]]]).tolist()[0][0]
                if cos_sim > 0.4:
                    satisfying_docs.append([doc[0], 0.8+0.05/len(query_words)*doc[1]+0.15*cos_sim])
        sorted_satisfying_docs = sorted(satisfying_docs, key=lambda x: x[1], reverse = True)
        return sorted_satisfying_docs

In [17]:
# Method to check if the distance between words is less than step and they are in the correct order
# It reminds a bit dfs, so named this way
def dfs(pos_list, list_num, list_element, step):
    cur_num = pos_list[list_num][list_element]
    if list_num == len(pos_list)-1:
        return True
    interval = bisect.bisect_right(pos_list[list_num+1], cur_num)
    if interval == len(pos_list[list_num+1]):
        if list_num != 0:
            return False
        if list_element == len(pos_list[list_num])-1:
            return False
        return dfs(pos_list,list_num, list_element+1,step)
    interval_step = bisect.bisect_right(pos_list[list_num+1], cur_num+step)
    if interval_step == 0:
        if list_num != 0:
            return False
        if list_element == len(pos_list[list_num])-1:
            return False
        return dfs(pos_list,list_num, list_element+1,step)
    for i in range(interval,interval_step):
        if dfs(pos_list, list_num+1, i, step):
            return True
    return False

In [18]:
# Method for counting for each document how many words from query appear in it
def count_frequency(my_list):   
    # Creating an empty dictionary  
    freq = {} 
    for items in my_list: 
        freq[items] = my_list.count(items) 
    sorted_by_value = sorted(freq.items(), key=lambda kv: kv[1], reverse = True)
    return sorted_by_value

In [20]:
# Example
search_index("tell me something about eminem", step = 2)

[[5574, 0.9186989794174831],
 [1627, 0.9147685597340267],
 [2133, 0.9081927220026653],
 [4381, 0.906945628921191],
 [2491, 0.9066063563028972],
 [4050, 0.9019745657841366],
 [1177, 0.9015039006868999],
 [295, 0.9013369778792064],
 [3990, 0.9007524887720745],
 [3663, 0.8987392226854961],
 [289, 0.8985218296448391],
 [476, 0.8984539608160655],
 [4175, 0.8975523630777996],
 [28, 0.8975225726763408],
 [3420, 0.89680921236674],
 [2068, 0.8965177098910014],
 [4794, 0.8960281352202099],
 [5059, 0.8948420802752178],
 [362, 0.8944798390070599],
 [288, 0.894023961822192],
 [3962, 0.8938817868630092],
 [1985, 0.8933249334494274],
 [1543, 0.8919709901014965],
 [849, 0.8915424535671871],
 [1387, 0.8911861399809521],
 [2195, 0.8911194602648418],
 [2229, 0.8907941217223804],
 [49, 0.8903597916165988],
 [3713, 0.8893434042731921],
 [2354, 0.8883525336782139],
 [99, 0.8879557366172474],
 [189, 0.8873633484045665],
 [5182, 0.8873284439245861],
 [4542, 0.8869081060091656],
 [469, 0.8869032422701518],
 [4

In [21]:
# Example of dictionary entry
dictionary["lightning"]

[[4291, 555, 4619, 2850, 2850, 5325, 2707, 1197, 1197, 1390],
 [4, 16, 5, 2, 9, 6, 4, 2, 5, 5]]

### Ranking part (pre-processing)

Should not be run in the app itself, information is taken from files.

In [75]:
# Getting the vectors for all documents, probably, should be stored as well as the index
doc_vectors = {}
for row in all_documents:
    doc_vectors.update({row['doc_id']: doc2vec(row['clean_data'].split())})

doc_vectors_idf = {}
for row in all_documents:
    doc_vectors_idf.update({row['doc_id']: doc2vec_idf(row['clean_data'].split())})

with open('docs_vectors_idf_8facts.pk', 'wb') as fp:
    pickle.dump(doc_vectors_idf, fp)
        
with open('docs_vectors_8facts.pk', 'wb') as fp:
    pickle.dump(doc_vectors, fp)

0.4


### Search for the Closest documents based on word2vec

In [22]:
def find_closest_docs_to_vector(vector, results_num,sim_limit):
    doc_ids = list(doc_vectors_idf.keys())
    doc_vecs = list(doc_vectors_idf.values())
    res = np.hstack(cosine_similarity(doc_vecs, [vector]))
    res_docs = (-res).argsort()[:results_num]
    return [[doc_ids[i], res[i]] for i in res_docs if res[i] > sim_limit]

# Method to find the closest 10 documents given string and the number of results
def find_closest_doc_to_vocabulary_entry(string, results_num, sim_limit):
    return find_closest_docs_to_vector(model[string], results_num, sim_limit)
    
# Method to get the closest documents to the query
# For the single word query uses the previous method for the query itself and capitalized query
# For long queries searches for the whole query in word2vec, for capitalized query
# Later converts query to the vector and searches the closest document to it
def closest_documents(query, results_num = 10, sim_limit = 0.4):
    query = clean_query(query)
    query_words = query.split()
    lemmatized_query = lemmatize_query(query_words)
    full_query_string = "_".join(query_words)
    if len(query_words) > 1:
        if full_query_string in model.vocab:
            return find_closest_doc_to_vocabulary_entry(full_query_string, results_num, sim_limit)
        capitalized_query = "_".join([word.capitalize() for word in query_words])
        if capitalized_query in model.vocab:
            return find_closest_doc_to_vocabulary_entry(capitalized_query, results_num, sim_limit)
    if len(query_words) == 1:
        if query in model.vocab:
            return find_closest_doc_to_vocabulary_entry(query, results_num, sim_limit)
        else:
            if query.capitalize() in model.vocab:
                return find_closest_doc_to_vocabulary_entry(query.capitalize(), results_num, sim_limit)
            return []
    query_vector = doc2vec_idf(lemmatized_query)
    return find_closest_docs_to_vector(query_vector, results_num, sim_limit)

In [23]:
# Example of similarity between doc2vec and doc2vec_idf
cosine_similarity([doc2vec_idf(["life"])],[doc2vec(["life"])])

array([[0.99999994]], dtype=float32)

In [24]:
# max idf value which is used if the word from query not in dictionary
max(idf_dict.values())

8.648221453822641

In [66]:
# Just all the doc_vectors, not for running (takes long time)
doc_vectors

{1239: array([ 7.50732422e-02, -3.50952148e-02, -8.78906250e-02,  1.43798828e-01,
         9.86938477e-02,  9.10644531e-02,  3.07865143e-02, -7.98950195e-02,
         4.10156250e-02,  9.79614258e-03,  3.05175781e-02, -1.07376099e-01,
        -1.44409180e-01,  2.36450195e-01, -9.46044922e-03,  1.87866211e-01,
         6.74438477e-02,  1.38259888e-01,  9.06372070e-02, -4.24804688e-02,
        -9.82666016e-02, -6.16455078e-02, -9.38110352e-02,  3.99169922e-02,
         3.81469727e-03, -5.10864258e-02, -1.09985352e-01,  7.17468262e-02,
         1.03271484e-01, -1.03866577e-01,  3.22570801e-02, -5.88684082e-02,
        -1.08520508e-01, -6.11419678e-02, -7.18383789e-02, -1.22314453e-01,
         1.05102539e-01, -5.51757812e-02, -7.47680664e-03,  1.45599365e-01,
         7.82470703e-02, -2.62756348e-02, -3.02124023e-02, -6.34765625e-02,
         3.22875977e-02, -8.38623047e-02,  2.78320312e-02,  1.38854980e-01,
        -1.19903564e-01,  1.03393555e-01,  2.96936035e-02,  2.07881927e-02,
      

### Search in ML results

In [25]:
# Read all the topics from database
with connection.cursor() as cursor:
        sql = "SELECT * from target_matrix"
        cursor.execute(sql)
        all_topics_distribution = cursor.fetchall()

In [26]:
# Constructing the dictionaries which will be used later
topics = np.unique([row['topic'] for row in all_topics_distribution])
topics_to_docs = {key: [[],[]] for key in topics}
for row in all_topics_distribution:
    topics_to_docs[row['topic']][0].append(row['doc_id'])
    topics_to_docs[row['topic']][1].append(row['score'])
    
topic_list = {key: doc2vec_idf(key.split()) for key in topics}

In [29]:
# Functions for retrieval from ML part
def find_closest_topics_to_vector(vector, results_num,sim_limit):
    topic_ids = list(topic_list.keys())
    topic_vecs = list(topic_list.values())
    res = np.hstack(cosine_similarity(topic_vecs, [vector]))
    res_topics = (-res).argsort()[:results_num]
    return [[topic_ids[i], res[i]] for i in res_topics if res[i] > sim_limit]

def closest_topic(query, results_num = 2, sim_limit = 0.5, score_limit = 0.5):
    if query in topic_list.keys():
        return [[topics_to_docs[query][0][i], topics_to_docs[query][1][i]] for i in len(topics_to_docs[query][0])]
    query_vector = doc2vec_idf(query.split())
    closest_topics = find_closest_topics_to_vector(query_vector, results_num, sim_limit)
    final_topics_docs = []
    for topic in closest_topics:
        final_topics_docs.extend([topics_to_docs[topic[0]][0][i], topic[1]*topics_to_docs[topic[0]][1][i]] 
                                 for i in range(0,len(topics_to_docs[topic[0]][0]))
                                if topics_to_docs[topic[0]][1][i] > score_limit)
    return final_topics_docs

In [30]:
# Example
closest_topic("time",2,0.5,0.7)

[[639, 0.5178201150125266],
 [2344, 0.4721303198837638],
 [1583, 0.4721169170077443],
 [423, 0.47213153832703825],
 [33, 0.5178304717803598],
 [1997, 0.49954529355996846],
 [2044, 0.47211326167792084],
 [1415, 0.47211508934283253],
 [66, 0.43514577872908117],
 [320, 0.41127400452661517],
 [85, 0.4112655135769844],
 [235, 0.47097705548644064],
 [1366, 0.41126922836744784],
 [2422, 0.4510625944962502],
 [1118, 0.4510758616050482],
 [1596, 0.4510641865493059],
 [1311, 0.4112633908395767],
 [1013, 0.4351415332542658],
 [231, 0.41126498289263247],
 [2592, 0.43514577872908117]]

### Combining all 3 approaches to get the final result

In [31]:
# Combining both search methods to get results
def get_results_for_query(query):
    index_search_result = search_index(query)
    closest_documents_result = closest_documents(query)
    closest_topic_result = closest_topic(query)
    docs_id_index = [doc_rank[0] for doc_rank in index_search_result]
    docs_id_closest = [doc_rank[0] for doc_rank in closest_documents_result]
    docs_id_topics = [doc_rank[0] for doc_rank in closest_topic_result]
    new_docs_from_topics = set(docs_id_topics).difference(set(docs_id_index))
    new_docs_from_closiness = set(docs_id_closest).difference(new_docs_from_topics.union(set(docs_id_index)))
    final_result = index_search_result
    for doc_rank in closest_topic_result:
        if doc_rank[0] in new_docs_from_topics:
            final_result.append(doc_rank)
    for doc_rank in closest_documents_result:
        if doc_rank[0] in new_docs_from_closiness:
            final_result.append(doc_rank)
    query_words = query.split()
    corrected_query = query_words
    for i, word in enumerate(query_words):
        if not word in model.vocab:
            corrected_query[i] = spell.correction(word)
    if query_words == corrected_query:
        return sorted(final_result, key=lambda x: x[1], reverse = True)
    else:
        corrected_results = get_results_for_query(" ".join(corrected_query))
        docs_id_original = [doc_rank[0] for doc_rank in final_result]
        docs_id_corrected = [doc_rank[0] for doc_rank in corrected_results]
        new_docs = set(docs_id_corrected).difference(set(docs_id_original))
        for result in corrected_results:
            if result[0] in new_docs:
                result[1] = result[1]*3/4
                final_result.append(result)
        return sorted(final_result, key=lambda x: x[1], reverse = True)

In [33]:
# Example of limitation of query cleaning
clean_query("to be or not to be")

''

In [34]:
# Example
get_results_for_query("swan lake")

[[845, 0.9125107347965241],
 [5183, 0.9081686764955521],
 [4576, 0.9000770419836045],
 [3417, 0.8997598886489869],
 [437, 0.8988808527588845],
 [1897, 0.8891262397170068],
 [4613, 0.42534565102060606]]

In [35]:
# Example of reading from database to check the results
with connection.cursor() as cursor:
        sql = "SELECT * from noisy_text where doc_id = 4613"
        cursor.execute(sql)
        print(cursor.fetchall())

[{'doc_id': 4613, 'noisy_data': ':9  ONE OF NICKI MINAJ’S DANCERS WAS BITTEN BY A SNAKE DURING A REHEARSAL FOR THE VMA PERFORMANCE OF “ANACONDA”. #8FACT  KNOW WHAT YOU DON’T KNOW by 8FACT.COM', 'insert_dt': datetime.datetime(2019, 3, 29, 11, 4, 41)}]


In [37]:
# Example of spell correction
spell.correction("Shortcaller")

'Shortcaller'

In [38]:
# Examples of clean_query
clean_query("lightning storm")

'lightning storm'

In [39]:
# Example of pos_tagging
pos_tag(["I", "ran", "into", "Marco"])

[('I', 'PRP'), ('ran', 'VBD'), ('into', 'IN'), ('Marco', 'NNP')]

### Lemmatizing, stemming, tokenization (and so on)

Taken from Oleg, not in use now but I keep it here in case I will suddenly need it

In [18]:
nltk.download()

showing info https://raw.githubusercontent.com/nltk/nltk_data/gh-pages/index.xml


True

In [16]:
stopwords = nltk.corpus.stopwords.words('english')

In [17]:
spell = SpellChecker()

In [18]:
stemmer = SnowballStemmer("english")

In [81]:
import re
def tokenize_and_stem(query):
    tokens = [word for word in nltk.word_tokenize(query)]
    stems = " ".join([stemmer.stem(t) for t in tokens])
    return stems

In [41]:
word2vec_dict = list(model.vocab.keys())

In [50]:
sep_words = [w.replace('_', ' ') for w in word2vec_dict]

In [114]:
stemmed_word2vec_new = []
for entry in sep_words:
    entry_stemmed = tokenize_and_stem(entry)
    stemmed_word2vec_new.append(entry_stemmed)

In [116]:
import pickle

with open('stemmed_word2vec', 'wb') as fp:
    pickle.dump(stemmed_word2vec_new, fp)

In [ ]:
with open ('stemmed_word2vec', 'rb') as fp:
    stemmed_word2vec_new = pickle.load(fp)

In [119]:
from nltk.stem import WordNetLemmatizer
wordnet_lemmatizer = WordNetLemmatizer()
sentence = "He was running and eating at same time. He has bad habit of swimming after playing long hours in the Sun."
punctuations="?:!.,;"
sentence_words = nltk.word_tokenize(sentence)
for word in sentence_words:
    if word in punctuations:
        sentence_words.remove(word)

In [184]:
spell.correction("Transatlantica")

AttributeError: 'function' object has no attribute 'correction'

In [154]:
wordnet_lemmatizer.lemmatize("Authors", pos = "n")

'Authors'